In [33]:
import pandas as pd
import numpy as np

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', None)

### Import Data

In [34]:
# import results parquet
pqt = pd.read_parquet('part.0.parquet')

# parse timeseries and metadata
pqt_ts = pqt.loc[:, pqt.columns.str.startswith('out.')]
pqt_meta = pqt.loc[:, pqt.columns.str.startswith('in.')]

other_cols = list(set(pqt.columns) - set(pqt_meta.columns) - set(pqt_ts.columns))
pqt_other = pqt.loc[:, other_cols]
pqt_meta['puma'] = pqt_other['puma']

C:\Anaconda\lib\site-packages\ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.


### Metadata

In [35]:
# Checks if string is a float number
def isfloat(string):
    try:
        float(string)
        return True
    except:
        return False  

# Converts string values to int or float values if possible
def convert_to_numeric(s):
    if not type(s) == str:
        return s
    
    if s.isnumeric():
        return int(s)
    elif isfloat(s):
        return float(s)
    else:
        return s

In [36]:
# Enumerate values and convert to numeric if possible
enums = {col: [convert_to_numeric(s) for s in sorted(pqt_meta[col].unique())] for col in pqt_meta.columns}
enums_list = ['|'.join([str(elem) for elem in enum]) if enum is not None else None for enum in list(enums.values())] #format

# Store datatypes for each column
dtypes = {k: str(pd.Series(v).dtypes) for k, v in enums.items()}


In [37]:
df_meta = pd.DataFrame({'field_location': 'metadata', 
                        'field_name': pqt_meta.columns, 
                        'data_type': list(dtypes.values()),
                        'allowable_enumerations': enums_list})

dtype_map = {
    'float64': 'float',
    'int64': 'integer',
    'object': 'string',
    'bool': 'bool'
}

df_meta['data_type'] = df_meta['data_type'].map(dtype_map)
df_meta.loc[df_meta['data_type'] == 'bool', 'allowable_enumerations'] = 'True|False'

In [38]:
df_meta

field_location                                    field_name data_type  \
0         metadata                                       in.sqft     float   
1         metadata                                 in.ahs_region    string   
2         metadata                                 in.applicable      bool   
3         metadata              in.ashrae_iecc_climate_zone_2004    string   
4         metadata                    in.bathroom_spot_vent_hour    string   
5         metadata                                   in.bedrooms   integer   
6         metadata              in.building_america_climate_zone    string   
7         metadata                           in.cec_climate_zone    string   
8         metadata                                in.ceiling_fan    string   
9         metadata                            in.census_division    string   
10        metadata                       in.census_division_recs    string   
11        metadata                              in.census_region    string   
12        metadata                              in.clothes_dryer    string   
13        metadata                             in.clothes_washer    string   
14        metadata                    in.clothes_washer_presence    string   
15        metadata                              in.cooking_range    string   
16        metadata                           in.cooling_setpoint    string   
17        metadata                in.cooling_setpoint_has_offset    string   
18        metadata          in.cooling_setpoint_offset_magnitude    string   
19        metadata             in.cooling_setpoint_offset_period    string   
20        metadata                                   in.corridor    string   
21        metadata                                     in.county    string   
22        metadata                               in.dehumidifier    string   
23        metadata                                 in.dishwasher    string   
24        metadata                                  in.door_area    string   
25        metadata                                      in.doors    string   
26        metadata                                      in.ducts    string   
27        metadata                                      in.eaves    string   
28        metadata                           in.electric_vehicle    string   
29        metadata                        in.geometry_attic_type    string   
30        metadata   in.geometry_building_horizontal_location_mf    string   
31        metadata  in.geometry_building_horizontal_location_sfa    string   
32        metadata                 in.geometry_building_level_mf    string   
33        metadata          in.geometry_building_number_units_mf    string   
34        metadata         in.geometry_building_number_units_sfa    string   
35        metadata                 in.geometry_building_type_acs    string   
36        metadata              in.geometry_building_type_height    string   
37        metadata                in.geometry_building_type_recs    string   
38        metadata                        in.geometry_floor_area    string   
39        metadata                    in.geometry_floor_area_bin    string   
40        metadata                   in.geometry_foundation_type    string   
41        metadata                            in.geometry_garage    string   
42        metadata                           in.geometry_stories   integer   
43        metadata                  in.geometry_stories_low_rise    string   
44        metadata              in.geometry_wall_exterior_finish    string   
45        metadata                         in.geometry_wall_type    string   
46        metadata     in.geometry_wall_type_and_exterior_finish    string   
47        metadata                                     in.has_pv    string   
48        metadata                               in.heating_fuel    string   
49        metadata                           in.heating_setpoint    string   
50        metadata        

### Timeseries

In [41]:
df_ts = pd.DataFrame({'field_location': 'timeseries', 
                        'field_name': pqt_ts.columns, 
                        'data_type': [str(dtype) for dtype in pqt_ts.dtypes.values],
                        'allowable_enumerations': None})

df_ts['data_type'] = df_ts['data_type'].map(dtype_map)

### Data dictionary

In [30]:
df_data = pd.concat([df_meta, df_ts]).reset_index(drop=True)
df_data['allowable_enumerations'] = df_data['allowable_enumerations'].fillna('n/a')

In [32]:
df_data.to_csv('data_dictionary.tsv', sep='\t', index=False)

### Enumeration Dictionary

In [13]:
enum_dict = pd.DataFrame()
for col, enum_list in enums.items():
    df = pd.DataFrame(enum_list, index=[col]*len(enum_list), columns=['enumeration'])
    enum_dict = enum_dict.append(df)

enum_dict['enumeration_description'] = None

In [14]:
enum_dict.to_csv('enumeration_dictionary.tsv', sep='\t')